<a href="https://colab.research.google.com/github/pragmatic-philosopher09/Audio-Emotion-Analyzer-Through-Deep-Learning/blob/main/Phase_1_Primary_Preprocessing_of_Dataset_%2B_Feature_Extraction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Mounting Process**

In [ ]:
import numpy as np
import pandas as pd

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import warnings
warnings.filterwarnings('ignore')


In [ ]:
audio_path = '/content/drive/MyDrive/Datasets/Datasets/Actor_01/03-01-01-01-01-01-01.wav'


In [ ]:
import IPython.display as ipd
import librosa
import librosa.display
import pandas as pd
import numpy as np


In [ ]:
x,sr = librosa.load(audio_path)
ipd.Audio(audio_path)

# **Importing the Dataset**

In [ ]:
dataset = '/drive/MyDrive/Datasets/Datasets/audio_speech_actors_01-24/'


In [ ]:
import os


In [ ]:
actor_folders = os.listdir(dataset)
actor_folders.sort() 
actor_folders

FileNotFoundError: ignored

# **Creation of Dataframe**

In [ ]:
emotions = []
gender = []
actor_ID = []
file_path = []
for i in actor_folders:
    filename = os.listdir(dataset + i) #iterate over Actor folders
    for f in filename: # go through files in the corresponding Actor's folder
        part = f.split('.')[0].split('-')#We split the file name initially as['03-01-01-01-01-01-01','wav'];Now,the 0th element is converted as ['03','01','01','01','01','01','01']
        emotions.append(int(part[2])) #Since,the second element represents the emotion of the actor.
        actor_ID.append(int(part[6])) #Since,the sixth element represents the ID of the actor.
        bg = int(part[6])
        if bg%2 == 0:
            bg = "female" #Since,even IDs correspond to females.
        else:
            bg = "male"  #Since,odd IDs correspond to males.
        gender.append(bg)
        file_path.append(dataset + i + '/' + f)

In [ ]:
#Creating a dataframe:
audio_df = pd.DataFrame(emotions)
audio_df = audio_df.replace({1:'neutral', 2:'calm', 3:'happy', 4:'sad', 5:'angry', 6:'fear', 7:'disgust', 8:'surprise'})
audio_df = pd.concat([pd.DataFrame(gender),audio_df,pd.DataFrame(actor_ID)],axis=1)
audio_df.columns = ['Gender','Emotion','Actor_ID']
audio_df = pd.concat([audio_df,pd.DataFrame(file_path, columns = ['Path'])],axis=1)
audio_df


Gender   Emotion  Actor_ID  \
0       male      calm         1   
1       male      calm         1   
2       male      calm         1   
3       male      calm         1   
4       male      calm         1   
...      ...       ...       ...   
1435  female   disgust        24   
1436  female   disgust        24   
1437  female   disgust        24   
1438  female   disgust        24   
1439  female  surprise        24   

                                                   Path  
0     /content/drive/MyDrive/Datasets/audio_speech_a...  
1     /content/drive/MyDrive/Datasets/audio_speech_a...  
2     /content/drive/MyDrive/Datasets/audio_speech_a...  
3     /content/drive/MyDrive/Datasets/audio_speech_a...  
4     /content/drive/MyDrive/Datasets/audio_speech_a...  
...                                                 ...  
1435  /content/drive/MyDrive/Datasets/audio_speech_a...  
1436  /content/drive/MyDrive/Datasets/audio_speech_a...  
1437  /content/drive/MyDrive/Datasets/audio_speech_a...  
1438  /content/drive/MyDrive/Datasets/audio_speech_a...  
1439  /content/drive/MyDrive/Datasets/audio_speech_a...  

[1440 rows x 4 columns]

In [ ]:
pd.set_option('display.max_colwidth', -1)

audio_df.sample(10)

Gender   Emotion  Actor_ID  \
954   female  angry     16         
420   female  calm      8          
261   male    calm      5          
979   male    calm      17         
1426  female  disgust   24         
268   male    disgust   5          
715   female  disgust   12         
1220  male    happy     21         
692   female  fear      12         
648   male    surprise  11         

                                                                                             Path  
954   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_16/03-01-05-01-02-01-16.wav  
420   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_08/03-01-02-01-01-01-08.wav  
261   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_05/03-01-02-02-01-01-05.wav  
979   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_17/03-01-02-01-01-01-17.wav  
1426  /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_24/03-01-07-01-02-01-24.wav  
268   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_05/03-01-07-01-02-01-05.wav  
715   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_12/03-01-07-01-02-02-12.wav  
1220  /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_21/03-01-03-01-02-01-21.wav  
692   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_12/03-01-06-02-01-01-12.wav  
648   /content/drive/MyDrive/Datasets/audio_speech_actors_01-24/Actor_11/03-01-08-01-01-01-11.wav

In [ ]:
def extract_features(data):
    # ZCR
    result = np.array([])
    zcr = np.mean(librosa.feature.zero_crossing_rate(y=data).T, axis=0)
    result=np.hstack((result, zcr)) # stacking horizontally

    # Chroma_stft
    stft = np.abs(librosa.stft(data))
    chroma_stft = np.mean(librosa.feature.chroma_stft(S=stft, sr=sample_rate).T, axis=0)
    result = np.hstack((result, chroma_stft)) # stacking horizontally

    # MFCC
    mfcc = np.mean(librosa.feature.mfcc(y=data, sr=sample_rate).T, axis=0)
    result = np.hstack((result, mfcc)) # stacking horizontally

    # MelSpectogram
    mel = np.mean(librosa.feature.melspectrogram(y=data, sr=sample_rate).T, axis=0)
    result = np.hstack((result, mel)) # stacking horizontally
    
    return result

def get_features(path):
    # duration and offset are used to take care of the no audio in start and the ending of each audio files as seen above.
    data, sample_rate = librosa.load(path, duration=2.5, offset=0.6)
    
    # without augmentation
    res1 = extract_features(data)
    result = np.array(res1)
    
    return result

In [ ]:

path = np.array(audio_df.Path)[1]
data, sample_rate = librosa.load(path)

X, Y = [], []
for path, emotion in zip(audio_df.Path, audio_df.Emotion):
    feature = get_features(path)
    # for ele in feature:
    #     X.append(ele)
    #     Y.append(emotion)
    X.append(feature)
    Y.append(emotion)

In [ ]:
X


[array([ 1.63596824e-01,  5.46767950e-01,  6.12877786e-01,  6.92036390e-01,
         6.40127540e-01,  5.61661780e-01,  5.52791655e-01,  5.10496616e-01,
         4.99767363e-01,  5.28035760e-01,  5.97266257e-01,  7.34471262e-01,
         7.11075366e-01, -5.86881287e+02,  9.31440887e+01,  3.66557097e+00,
         2.21784401e+01,  1.18990374e+00,  1.02845659e+01, -1.12459784e+01,
        -5.04499435e+00, -1.64270096e+01, -6.05345964e+00, -2.39010715e+00,
         3.76437831e+00, -3.22580409e+00, -3.84119725e+00, -1.31321704e+00,
         4.70837057e-01, -1.16863537e+01, -1.75726902e+00, -4.61440229e+00,
         1.05182338e+00,  6.69522342e-06,  1.11321140e-04,  3.43407295e-03,
         6.23411871e-02,  6.13444783e-02,  2.56412732e-03,  7.71754305e-04,
         1.53018115e-02,  6.09079860e-02,  2.04190165e-02,  2.03358498e-03,
         2.35097576e-03,  1.10405050e-02,  1.51269175e-02,  1.04697859e-02,
         5.38798748e-03,  7.49221491e-03,  1.54744880e-02,  1.03128394e-02,
         4.5

In [ ]:
Features = pd.DataFrame(X)
Features['labels'] = Y
Features.to_csv('features.csv', index=False)
Features.head()

0         1         2         3         4         5         6  \
0  0.163597  0.546768  0.612878  0.692036  0.640128  0.561662  0.552792   
1  0.180714  0.530097  0.622458  0.716000  0.679560  0.632252  0.641911   
2  0.238779  0.613995  0.678766  0.713347  0.719922  0.652184  0.621229   
3  0.156566  0.626399  0.649439  0.679614  0.696834  0.635487  0.627616   
4  0.232661  0.613645  0.700953  0.730549  0.669780  0.641119  0.658767   

          7         8         9  ...       152       153       154       155  \
0  0.510497  0.499767  0.528036  ...  0.000022  0.000012  0.000016  0.000022   
1  0.614983  0.623660  0.628080  ...  0.000022  0.000012  0.000017  0.000021   
2  0.618404  0.642188  0.663469  ...  0.000012  0.000014  0.000020  0.000048   
3  0.645216  0.693452  0.660763  ...  0.000004  0.000003  0.000005  0.000009   
4  0.633846  0.671523  0.676698  ...  0.000006  0.000004  0.000012  0.000006   

        156       157       158           159           160  labels  
0  0.000032  0.000031  0.000009  9.023522e-07  1.228982e-08  calm    
1  0.000022  0.000016  0.000005  5.783323e-07  8.434678e-09  calm    
2  0.000073  0.000076  0.000033  2.593599e-06  2.282365e-08  calm    
3  0.000010  0.000010  0.000004  5.095087e-07  3.934685e-09  calm    
4  0.000004  0.000003  0.000001  9.604059e-08  1.924340e-09  calm    

[5 rows x 162 columns]

In [ ]:
Features.tail()

0         1         2         3         4         5         6  \
1435  0.220748  0.703223  0.666391  0.584437  0.440157  0.386922  0.364820   
1436  0.195918  0.508395  0.494076  0.568567  0.532038  0.514881  0.547499   
1437  0.194680  0.677356  0.536462  0.472717  0.421721  0.466479  0.472123   
1438  0.100988  0.422344  0.403276  0.372255  0.335838  0.353051  0.359522   
1439  0.210797  0.678509  0.615912  0.591720  0.544004  0.524419  0.566233   

             7         8         9  ...       152       153       154  \
1435  0.404838  0.463495  0.495361  ...  0.007261  0.006272  0.005089   
1436  0.565791  0.623200  0.608617  ...  0.001540  0.001429  0.001116   
1437  0.531564  0.513600  0.498205  ...  0.001198  0.001146  0.000856   
1438  0.501198  0.480794  0.427234  ...  0.000035  0.000028  0.000027   
1439  0.588347  0.637855  0.644205  ...  0.005657  0.004143  0.003528   

           155       156       157       158           159           160  \
1435  0.004384  0.002692  0.001821  0.000511  4.918412e-05  5.008941e-07   
1436  0.000725  0.000412  0.000205  0.000107  1.736855e-05  3.759612e-07   
1437  0.000762  0.000666  0.000424  0.000147  1.310377e-05  1.861763e-07   
1438  0.000014  0.000011  0.000009  0.000003  3.989984e-07  3.375928e-09   
1439  0.002775  0.002309  0.001547  0.000499  3.767177e-05  5.714054e-07   

        labels  
1435  disgust   
1436  disgust   
1437  disgust   
1438  disgust   
1439  surprise  

[5 rows x 162 columns]

In [ ]:
Features[161:]

0         1         2         3         4         5         6  \
161   0.201800  0.672631  0.714742  0.698151  0.638098  0.632057  0.664401   
162   0.197370  0.667736  0.674156  0.646716  0.692732  0.692367  0.632540   
163   0.131804  0.525087  0.639552  0.618162  0.558586  0.519902  0.514801   
164   0.152344  0.627404  0.697555  0.654034  0.600775  0.574069  0.581325   
165   0.157204  0.581864  0.709384  0.745085  0.680725  0.606044  0.588619   
...        ...       ...       ...       ...       ...       ...       ...   
1435  0.220748  0.703223  0.666391  0.584437  0.440157  0.386922  0.364820   
1436  0.195918  0.508395  0.494076  0.568567  0.532038  0.514881  0.547499   
1437  0.194680  0.677356  0.536462  0.472717  0.421721  0.466479  0.472123   
1438  0.100988  0.422344  0.403276  0.372255  0.335838  0.353051  0.359522   
1439  0.210797  0.678509  0.615912  0.591720  0.544004  0.524419  0.566233   

             7         8         9  ...       152       153       154  \
161   0.670628  0.753717  0.753288  ...  0.000122  0.000140  0.000127   
162   0.652249  0.671552  0.686961  ...  0.000421  0.000415  0.000377   
163   0.554177  0.588790  0.569586  ...  0.006282  0.009240  0.009500   
164   0.557404  0.578291  0.638758  ...  0.012606  0.010560  0.008038   
165   0.598262  0.628337  0.661037  ...  0.012550  0.017030  0.011490   
...        ...       ...       ...  ...       ...       ...       ...   
1435  0.404838  0.463495  0.495361  ...  0.007261  0.006272  0.005089   
1436  0.565791  0.623200  0.608617  ...  0.001540  0.001429  0.001116   
1437  0.531564  0.513600  0.498205  ...  0.001198  0.001146  0.000856   
1438  0.501198  0.480794  0.427234  ...  0.000035  0.000028  0.000027   
1439  0.588347  0.637855  0.644205  ...  0.005657  0.004143  0.003528   

           155       156       157       158           159           160  \
161   0.000181  0.000214  0.000124  0.000037  3.445602e-06  7.822305e-08   
162   0.000331  0.000272  0.000255  0.000161  2.057600e-05  3.471486e-07   
163   0.008862  0.009500  0.007869  0.002628  2.475040e-04  4.233591e-06   
164   0.011200  0.014464  0.008581  0.003662  2.849788e-04  4.508268e-06   
165   0.009939  0.011173  0.006405  0.001906  1.591639e-04  3.072923e-06   
...        ...       ...       ...       ...           ...           ...   
1435  0.004384  0.002692  0.001821  0.000511  4.918412e-05  5.008941e-07   
1436  0.000725  0.000412  0.000205  0.000107  1.736855e-05  3.759612e-07   
1437  0.000762  0.000666  0.000424  0.000147  1.310377e-05  1.861763e-07   
1438  0.000014  0.000011  0.000009  0.000003  3.989984e-07  3.375928e-09   
1439  0.002775  0.002309  0.001547  0.000499  3.767177e-05  5.714054e-07   

        labels  
161   disgust   
162   fear      
163   fear      
164   angry     
165   fear      
...    ...      
1435  disgust   
1436  disgust   
1437  disgust   
1438  disgust   
1439  surprise  

[1279 rows x 162 columns]

# **Creating the csv**

In [ ]:
# EXPORT TO CSV(Saving the dataframe as a csv file to the gdrive under the Dataset folder.)
audio_df.to_csv('/content/drive/MyDrive/Datasets/CSV_dataset')

# **MEL**

In [ ]:
# ITERATE OVER ALL AUDIO FILES AND EXTRACT LOG MEL SPECTROGRAM MEAN VALUES INTO DF FOR MODELING 
df = pd.DataFrame(columns=['mel_spectrogram'])

counter=0

for index,path in enumerate(audio_df.Path):
    X, sample_rate = librosa.load(path, res_type='kaiser_fast',duration=3,sr=44100,offset=0.5)

    #get the mel-scaled spectrogram and transform both the y-axis (frequency) to log scale, and the “color” axis (amplitude) to Decibels.
    spectrogram = librosa.feature.melspectrogram(y=X, sr=sample_rate, n_mels=128,fmax=8000) 
    db_spec = librosa.power_to_db(spectrogram)

    #temporally average spectrogram
    log_spectrogram = np.mean(db_spec, axis = 0)
  

    df.loc[counter] = [log_spectrogram]
    counter=counter+1   
#259 new Features have been created using the MEL Spectogram.
print(len(df))
df.head()

1440


mel_spectrogram
0  [-83.73174, -83.73174, -83.73174, -83.73174, -83.30041, -83.37535, -83.73174, -83.73174, -83.73174, -83.73174, -83.73174, -83.73174, -83.73174, -83.57985, -83.51394, -83.73174, -83.73174, -83.73174, -83.73174, -83.73174, -83.73174, -83.73174, -83.71066, -83.59938, -83.567024, -83.6743, -83.27724, -82.49633, -83.00421, -83.16834, -81.65792, -80.446754, -79.90101, -80.70154, -82.259926, -82.66486, -79.74067, -77.68163, -79.33032, -80.32808, -81.14637, -79.13109, -65.28074, -47.192448, -43.516964, -42.94589, -39.281166, -38.676147, -37.86402, -36.91663, -36.612595, -36.87283, -38.26445, -38.40952, -37.552742, -37.53131, -37.440453, -38.050446, -38.75265, -39.865376, -40.498913, -40.570835, -40.277878, -40.54298, -41.215088, -41.17698, -41.679302, -42.614677, -43.16011, -43.802498, -45.069096, -47.005543, -48.232697, -51.24373, -54.97208, -56.903114, -59.432182, -60.62913, -60.79472, -57.393925, -52.04683, -47.44, -44.63727, -42.553123, -42.017956, -42.761307, -43.279755, -43.042397, -42.28459, -41.699577, -40.42862, -40.330162, -40.69483, -42.462624, -45.003033, -45.533585, -46.134163, -47.3164, -48.750908, -49.784832, ...]                                
1  [-80.09864, -80.09864, -80.06536, -80.00435, -80.09864, -80.09864, -80.09864, -80.09864, -80.09864, -80.09864, -80.09864, -79.99587, -79.39695, -79.34011, -79.40979, -76.94761, -65.19479, -62.623806, -69.102135, -74.59703, -66.69237, -55.469032, -55.64762, -64.83025, -68.891045, -72.82557, -74.88806, -76.827065, -78.348335, -79.408165, -77.48786, -69.676636, -70.02172, -76.91606, -75.64207, -74.97173, -76.25741, -76.769226, -75.51826, -75.08402, -74.75239, -75.04328, -75.89109, -70.97349, -51.163506, -45.724106, -42.84073, -38.030857, -37.27417, -36.74388, -35.328304, -34.738266, -35.379715, -35.805737, -35.55549, -35.815628, -35.720867, -35.53038, -35.2414, -34.613667, -35.201866, -35.809692, -36.025337, -35.92121, -35.428497, -35.346737, -35.868767, -36.909573, -39.425976, -41.839314, -44.315094, -47.40493, -51.380306, -53.23794, -53.291237, -50.73282, -45.679058, -41.96244, -40.58939, -40.903473, -42.386578, -42.37782, -41.513874, -40.768627, -40.592167, -40.3051, -39.212425, -40.188183, -41.657917, -42.767273, -44.30909, -44.775726, -44.582447, -44.88151, -44.940666, -45.30056, -46.094353, -48.36287, -49.46987, -47.79803, ...]                      
2  [-79.611626, -79.611626, -79.611626, -79.611626, -79.611626, -79.611626, -79.611626, -79.61057, -79.611626, -79.55071, -79.39862, -79.58224, -79.611626, -79.611626, -79.6031, -79.609566, -79.611626, -79.61031, -79.57603, -79.36402, -79.2456, -79.5728, -79.611626, -79.10512, -78.06555, -78.34686, -79.32904, -79.611626, -79.38054, -76.99507, -69.494514, -67.42026, -71.6927, -77.55184, -78.59431, -77.33222, -76.805016, -75.72909, -73.67359, -73.63868, -73.795395, -73.32057, -53.179474, -41.105213, -39.716957, -37.364796, -34.027695, -32.77418, -31.813654, -31.809566, -31.427456, -31.59654, -32.039875, -31.86541, -32.457268, -33.20494, -33.50199, -33.63662, -34.00035, -34.491528, -34.89767, -35.608807, -37.031574, -38.848152, -38.970936, -39.801666, -42.11047, -44.88692, -48.342636, -52.33919, -54.593292, -55.269104, -48.771324, -45.47582, -46.22551, -46.426662, -46.93866, -44.73974, -42.745968, -40.82414, -37.879482, -37.48088, -38.519085, -39.358597, -39.506092, -39.928562, -40.66351, -41.11441, -40.952312, -40.562103, -40.204727, -41.16934, -42.07052, -43.061638, -43.627552, -42.98014, -41.427303, -40.834087, -42.27185, -38.925556, ...]                 
3  [-79.123436, -79.123436, -79.123436, -79.123436, -79.09168, -79.01513, -79.03472, -79.01186, -78.77649, -78.95222, -79.123436, -79.123436, -79.123436, -79.123436, -79.11889, -79.109184, -79.123436, -79.123436, -79.123436, -79.123436, -79.123436, -79.123436, -79.123436, -79.123436, -79.123436, -78.89392, -77.49061, -78.30837, -79.01086, -79.11719, -79.123436, -79.054436, -79.10984, -78.99883, -79.113525, -78.26577, -74.39272, -70.223404, -70.00315, -73.172

In [ ]:
df.tail(5)


mel_spectrogram
1435  [-59.609196, -59.128292, -59.56301, -61.30296, -61.619843, -61.774063, -62.131523, -62.65473, -62.494205, -62.513943, -62.470337, -62.602592, -62.40452, -62.137, -61.945717, -61.070324, -60.944813, -60.75309, -60.514748, -60.632607, -61.278145, -61.728046, -61.65632, -62.3047, -62.698635, -62.698635, -62.698635, -62.698635, -62.698635, -62.698635, -62.698635, -62.698635, -62.698635, -62.698635, -62.668316, -62.698635, -62.1906, -61.49062, -61.036743, -60.58985, -60.602947, -53.719646, -35.300102, -27.707882, -25.744143, -25.649092, -25.68051, -25.912186, -26.987486, -28.434402, -29.234194, -29.163353, -28.112259, -28.442772, -27.241241, -27.669573, -28.732393, -27.525011, -27.554861, -28.131426, -27.864594, -28.855085, -27.921402, -26.263035, -25.900156, -26.24278, -24.883553, -24.846859, -25.70484, -26.277363, -30.023773, -36.215286, -40.13318, -41.810333, -43.758873, -41.882145, -34.620937, -30.166693, -31.211113, -32.920937, -33.971786, -34.32194, -34.365482, -34.701057, -34.477352, -33.349873, -31.66208, -29.47181, -29.036745, -30.228024, -31.062656, -31.278708, -29.600508, -27.782187, -26.650846, -25.052584, -24.331938, -23.794573, -23.724876, -24.398487, ...]
1436  [-66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.5537, -66.284515, -66.00498, -66.23658, -66.33482, -65.85104, -41.1648, -30.195799, -25.332857, -24.050617, -23.70272, -23.81385, -24.099222, -25.17898, -26.39173, -27.957727, -28.010683, -28.150846, -27.475664, -28.193138, -27.077984, -26.519703, -25.822247, -25.52113, -26.612719, -26.444311, -25.340473, -24.571932, -24.664984, -24.877422, -26.04755, -27.942608, -29.994278, -33.87219, -38.137493, -41.111923, -43.841557, -45.23607, -47.12059, -41.21211, -34.677185, -34.188786, -37.33943, -37.33989, -37.15642, -37.379425, -37.5923, -38.228592, -37.887157, -36.76155, -36.561893, -36.31275, -34.074017, -31.948296, -31.648098, -32.466892, -32.605442, -33.083492, -33.302067, -33.077812, -31.435328, -29.950666, -28.857819, -29.25821, ...]                                                                            
1437  [-59.71533, -59.487312, -58.76509, -58.078213, -57.865845, -57.900227, -56.573124, -57.192963, -57.220287, -56.616825, -55.91967, -54.76017, -54.88878, -54.740543, -54.12245, -54.520435, -54.005173, -53.66445, -53.86428, -54.863026, -54.40815, -54.28299, -54.722584, -55.884075, -55.69597, -55.857407, -56.58984, -58.016876, -59.176826, -60.46755, -61.333813, -61.486324, -61.486324, -61.486324, -61.486324, -61.486324, -61.486324, -61.486324, -61.486324, -61.486324, -61.406322, -59.99904, -41.156593, -33.72192, -33.003284, -28.24071, -24.803543, -25.940937, -27.145468, -27.862907, -28.898756, -29.746763, -30.328009, -30.533304, -30.472048, -29.963913, -28.690678, -27.944904, -26.047318, -21.902653, -20.89508, -20.669235, -21.736729, -23.520876, -24.756021, -25.365135, -26.323095, -27.511526, -28.951328, -30.435005, -32.192497, -33.472317, -32.413548, -32.973347, -36.774384, -41.19091, -43.171383, -44.458942, -45.562294, -45.86381, -43.07566, -41.018917, -40.923126, -39.974106, -38.401318, -36.471546, -34.84412, -34.745914, -34.312824, -32.7534, -31.944304, -32.645844, -30.85746, -29.31489, -30.188274, -33.59878, -35.988464, -37.156834, -36.074917, -32.972298, ...]    
1438  [-67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, -67.63433, 

In [ ]:
print(counter)
print(spectrogram.shape)
print(db_spec.shape)
print(log_spectrogram.shape)
len(log_spectrogram)
log_spectrogram

1440
(128, 259)
(128, 259)
(259,)


array([-45.20008 , -43.823227, -44.344135, -45.735912, -46.09555 ,
       -45.702065, -45.733982, -46.31748 , -47.4251  , -48.189823,
       -48.735435, -49.60999 , -51.1141  , -51.74185 , -52.354496,
       -54.285336, -55.315113, -56.219368, -57.39988 , -58.403313,
       -58.453056, -59.335632, -61.146473, -61.302254, -61.302254,
       -61.302254, -61.302254, -61.302254, -61.302254, -61.302254,
       -61.302254, -61.302254, -61.302254, -61.243004, -61.2198  ,
       -61.302254, -61.302254, -61.296875, -61.115505, -60.799633,
       -60.77148 , -60.81766 , -35.838463, -22.9393  , -18.907736,
       -18.616055, -18.044601, -19.23666 , -20.700382, -22.054058,
       -22.832083, -22.12616 , -20.604311, -18.693512, -17.709837,
       -18.46701 , -19.365866, -19.295439, -17.838974, -16.967148,
       -18.129576, -20.528646, -23.19548 , -26.699417, -30.614357,
       -36.81162 , -39.28457 , -39.476093, -39.06205 , -33.14839 ,
       -28.453377, -28.692339, -31.439083, -32.63149 , -32.337

# **Concatenating coloumns**

In [ ]:
# TURN ARRAY INTO LIST AND JOIN WITH AUDIO_DF TO GET CORRESPONDING EMOTION LABELS
df_combined = pd.concat([audio_df,pd.DataFrame(df['mel_spectrogram'].values.tolist())],axis=1)
df_combined = df_combined.fillna(0)
     


In [ ]:
# DROP PATH COLUMN FOR MODELING
df_combined.drop(columns='Path',inplace=True)
df_combined.head()

Gender Emotion  Actor_ID          0          1          2          3  \
0  male   calm    1        -83.731743 -83.731743 -83.731743 -83.731743   
1  male   calm    1        -80.098640 -80.098640 -80.065361 -80.004349   
2  male   calm    1        -79.611626 -79.611626 -79.611626 -79.611626   
3  male   calm    1        -79.123436 -79.123436 -79.123436 -79.123436   
4  male   calm    1        -80.147774 -80.147774 -80.147774 -80.147774   

           4          5          6  ...        249        250        251  \
0 -83.300407 -83.375351 -83.731743  ... -67.309311 -68.202721 -70.755356   
1 -80.098640 -80.098640 -80.098640  ... -79.883743 -80.098640 -80.098640   
2 -79.611626 -79.611626 -79.611626  ... -79.611626 -79.611626 -79.611626   
3 -79.091682 -79.015129 -79.034721  ... -76.827530 -76.330978 -77.452744   
4 -80.147774 -80.147774 -80.147774  ... -80.147774 -80.147774 -80.122353   

         252        253        254        255        256        257        258  
0 -70.574722 -70.424881 -72.304726 -73.052025 -75.970840 -78.337257 -77.129829  
1 -80.053177 -80.028328 -79.989746 -80.051186 -80.086296 -79.897224 -79.750397  
2 -79.611626 -79.611626 -79.595642 -79.611626 -79.611626 -79.611626 -79.611626  
3 -78.737953 -78.958054 -78.833527 -79.081268 -79.123436 -79.123436 -79.123436  
4 -79.998413 -80.119652 -80.147774 -80.130814 -80.015106 -80.147774 -80.147774  

[5 rows x 262 columns]

In [ ]:
df_combined.tail(5)


Gender   Emotion  Actor_ID          0          1          2          3  \
1435  female  disgust   24       -59.609196 -59.128292 -59.563011 -61.302959   
1436  female  disgust   24       -66.553703 -66.553703 -66.553703 -66.553703   
1437  female  disgust   24       -59.715328 -59.487312 -58.765091 -58.078213   
1438  female  disgust   24       -67.634331 -67.634331 -67.634331 -67.634331   
1439  female  surprise  24       -45.200081 -43.823227 -44.344135 -45.735912   

              4          5          6  ...        249        250        251  \
1435 -61.619843 -61.774063 -62.131523  ... -39.059666 -39.546139 -39.909985   
1436 -66.553703 -66.553703 -66.553703  ... -60.790161 -61.347542 -62.645752   
1437 -57.865845 -57.900227 -56.573124  ... -32.094276 -31.967630 -30.905954   
1438 -67.634331 -67.634331 -67.634331  ... -51.370712 -52.471832 -53.571259   
1439 -46.095551 -45.702065 -45.733982  ... -61.288383 -61.167412 -61.030792   

            252        253        254        255        256        257  \
1435 -41.021275 -42.025219 -41.798702 -41.807014 -42.457993 -43.402321   
1436 -63.085438 -62.377399 -62.193592 -62.928299 -64.024933 -64.527260   
1437 -32.003017 -32.739891 -33.646950 -35.173309 -35.692657 -36.192184   
1438 -53.870922 -55.599457 -58.315693 -60.070503 -59.134911 -56.666817   
1439 -60.673954 -60.724171 -60.863770 -60.995415 -61.174271 -61.302254   

            258  
1435 -45.924473  
1436 -63.976532  
1437 -37.507820  
1438 -56.372982  
1439 -61.302254  

[5 rows x 262 columns]

# **creation of Train and test data**




In [ ]:
# TRAIN TEST SPLIT DATA
from sklearn.model_selection import train_test_split
train,test = train_test_split(df_combined, test_size=0.2, random_state=0,
                               stratify=df_combined[['Emotion','Gender','Actor_ID']])
     

In [ ]:
#TRAINING SET
X_train = train.iloc[:, 3:] #Considering only the features here (they start from the 3rd column.)
y_train = train.iloc[:,:2].drop(columns=['Gender'])#Since we need only want to identify the emotion,we have used this.
print(X_train.shape)
print(X_train)

#TESTING SET
X_test = test.iloc[:,3:]
y_test = test.iloc[:,:2].drop(columns=['Gender'])
print(X_test.shape)
print(X_test)

(1152, 259)
              0          1          2          3          4          5  \
706  -52.100067 -52.100067 -52.100067 -52.100067 -52.100067 -52.100067   
454  -67.447556 -67.421524 -67.535553 -67.255875 -67.267403 -67.356262   
1291 -68.620537 -68.490273 -68.540733 -68.602585 -68.772194 -68.801872   
1439 -45.200081 -43.823227 -44.344135 -45.735912 -46.095551 -45.702065   
882  -64.114433 -64.158646 -64.153778 -63.828480 -63.921379 -63.949814   
...         ...        ...        ...        ...        ...        ...   
1227 -55.351234 -54.636051 -54.561520 -55.446495 -55.953838 -56.111977   
1107 -66.688820 -66.651588 -67.557388 -67.570740 -67.881104 -68.421829   
15   -79.944633 -79.944633 -79.944633 -79.944633 -79.944633 -79.944633   
602  -81.669090 -80.576149 -80.469734 -80.275307 -78.723099 -78.325089   
26   -69.923248 -69.971130 -69.971130 -69.920120 -69.685768 -69.406624   

              6          7          8          9  ...        249        250  \
706  -52.100067 -52.

In [ ]:
# NORMALIZE DATA
mean = np.mean(X_train, axis=0)
std = np.std(X_train, axis=0)
X_train = (X_train - mean)/std
X_test = (X_test - mean)/std
     

# **One hot Encoding**

In [ ]:
# ONE HOT ENCODE THE TARGET
# CNN REQUIRES INPUT AND OUTPUT ARE NUMBERS
from sklearn.preprocessing import LabelEncoder
from tensorflow.keras.utils import to_categorical
lb = LabelEncoder()
y_train = to_categorical(lb.fit_transform(y_train))
y_test = to_categorical(lb.fit_transform(y_test))

print(y_test[0:10])
#Since,there are 8 different emotions; we get 8 columns.
#The places where 1 is present represents that particular emotion.

[[0. 0. 0. 1. 0. 0. 0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 1. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 1. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 0. 1. 0. 0.]
 [1. 0. 0. 0. 0. 0. 0. 0.]]


In [ ]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import StandardScaler

X = Features.iloc[: ,:-1].values
y = Features['labels'].values

encoder = OneHotEncoder()
y = encoder.fit_transform(np.array(y).reshape(-1,1)).toarray()

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2,random_state=0, shuffle=True)

scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)
     

In [ ]:
X_train.shape, y_train.shape, X_test.shape, y_test.shape


((1152, 161), (1152, 8), (288, 161), (288, 8))